In [1]:
%matplotlib qt
import numpy as np
import matplotlib.pyplot as plt
import random
from matplotlib.animation import FFMpegWriter

# Constants
maxX, maxY = 100, 100
nDots = 100
maxPeopleAtExhibit = 5
waiting_duration = 10
start_delay = 1  # Delay between each dot starting

# Environment setup
A = np.zeros((maxX, maxY))
entrance = (maxX - 1, maxY // 2)
exit = (0, maxY // 2)

# Define exhibits
exhibits = [(75, 75), (75, 25), (25, 75), (25, 25)]
for ex in exhibits:
    A[ex] = 2

# Initialize dots with a delay
dots = {}
for i in range(nDots):
    random_exhibits = random.sample(exhibits, random.randint(1, len(exhibits)))  # Random subset of exhibits
    dots[i] = {'position': entrance, 'delay': i * start_delay, 'to_visit': random_exhibits, 'waiting_time': 0}
visited = {i: [] for i in range(nDots)}
waiting_time = {i: 0 for i in range(nDots)}
exhibit_visitors = {ex: 0 for ex in exhibits}

def display(A, dots, ax):
    ax.clear()
    ax.imshow(A.T, cmap='gray')
    if dots:
        x, y = zip(*[dot['position'] for dot in dots.values()])
        ax.scatter(x, y, c='red', s=1)
    ax.axis('off')
    fig.canvas.draw()

def is_valid_move(x, y):
    return 0 <= x < maxX and 0 <= y < maxY and A[x, y] != 1

def move_dot(dot, target):
    x, y = dot
    dx, dy = np.sign(target[0] - x), np.sign(target[1] - y)
    if random.random() < 0.9:
        new_x, new_y = x + dx, y + dy
    else:
        new_x, new_y = x + random.choice([-1, 0, 1]), y + random.choice([-1, 0, 1])
    if is_valid_move(new_x, new_y):
        return (new_x, new_y)
    return dot

def find_closest_exhibit(dot, visited_exhibits):
    min_distance = float('inf')
    closest_exhibit = None
    for exhibit in exhibits:
        if exhibit not in visited_exhibits and exhibit_visitors[exhibit] < maxPeopleAtExhibit:
            distance = np.linalg.norm(np.array(dot) - np.array(exhibit))
            if distance < min_distance:
                min_distance = distance
                closest_exhibit = exhibit
    return closest_exhibit

def next_target(dot_id, dot, to_visit):
    # If the dot is at the exit and has visited all desired exhibits
    if not to_visit and dot == exit:
        return exit

    # Find the closest unvisited exhibit from the dot's to_visit list
    min_distance = float('inf')
    closest_exhibit = None
    for exhibit in to_visit:
        distance = np.linalg.norm(np.array(dot) - np.array(exhibit))
        if distance < min_distance:
            min_distance = distance
            closest_exhibit = exhibit

    # If there's an unvisited exhibit left, return it as the next target
    if closest_exhibit:
        return closest_exhibit

    # If no more exhibits to visit, return the exit
    return exit

def update_dots(dots, visited, exhibit_visitors):
    new_dots = {}
    for dot_id, dot_info in dots.items():
        dot_pos, delay, to_visit, waiting_time = dot_info.values()

        # Handle initial delay
        if delay > 0:
            dot_info['delay'] -= 1
            new_dots[dot_id] = dot_info
            continue

        # Handle waiting at an exhibit
        if waiting_time > 0:
            waiting_time -= 1
            dot_info['waiting_time'] = waiting_time
            if waiting_time > 0:
                new_dots[dot_id] = dot_info
                continue

        target = next_target(dot_id, dot_pos, to_visit)
        new_dot_pos = move_dot(dot_pos, target)
        
        if A[new_dot_pos] == 2 and new_dot_pos not in visited[dot_id]:
            visited[dot_id].append(new_dot_pos)
            dot_info['waiting_time'] = random.randint(5, 20)  # Random wait time
            if new_dot_pos in to_visit:
                to_visit.remove(new_dot_pos)  # Safely remove the exhibit from to_visit
            exhibit_visitors[new_dot_pos] += 1
        elif A[dot_pos] == 2 and dot_pos != new_dot_pos:
            if exhibit_visitors[dot_pos] > 0:
                exhibit_visitors[dot_pos] -= 1

        dot_info['position'] = new_dot_pos

        # Check if the dot has reached the exit and visited all its desired exhibits
        if new_dot_pos == exit and not to_visit:
            continue  # Dot exits the simulation

        new_dots[dot_id] = dot_info

    return new_dots, visited, exhibit_visitors

# Simulation
metadata = dict(title='100 Dots Simulation Random', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig, ax = plt.subplots()

with writer.saving(fig, "100dots_random2.mp4", dpi=200):
    while dots:
        dots, visited, exhibit_visitors = update_dots(dots, visited, exhibit_visitors)
        display(A, dots, ax)
        plt.pause(0.1)
        writer.grab_frame()
